# Transform IUPAC names into numerical data.

In [1]:
import pandas as pd

# Upload dataset as data frame
df_cids =pd.read_csv('df4_targets.csv', index_col=[0])

# To avoid truncation of some columns during data frame display
pd.set_option('display.max_columns', None) 

# Display the data frame
print('Shape of the data frame: ', df_cids.shape)
df_cids.head()

Shape of the data frame:  (53538, 2)


UPAC  target
0  ethyl 1-amino-7,8,8-trimethyl-5-morpholin-4-yl...       0
1  N-[2-(1H-indol-3-yl)ethyl]-2-oxochromene-3-car...       0
2  6-chloro-7-hydroxy-3,4-dimethyl-8-(piperidin-1...       0
3  4-chloro-N-[[1-(dimethylamino)cyclohexyl]methy...       0
4  1-[[4-(2-oxopyrrolidin-1-yl)phenyl]methyl]-3-p...       0

In [2]:
df_cids = df_cids.dropna()
df_cids.shape

(53538, 2)

In [3]:
df_cids = df_cids.drop_duplicates()
df_cids.shape

(53536, 2)

In [4]:
df_cids = df_cids[df_cids['UPAC'].notna()]
df_cids['UPAC'] = df_cids['UPAC'].astype('string') 
df_cids.dtypes

UPAC      string[python]
target             int64
dtype: object

In [5]:
# make a copy to use latter for connection aiwth smiles 
df_iupac_target = df_cids.copy()

In [6]:
# Obtain listo fo UPAC formulas provided in PubChem
UPAC_list = df_cids['UPAC'].to_list()

for item in UPAC_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

ethyl 1-amino-7,8,8-trimethyl-5-morpholin-4-yl-6,9-dihydrothieno[2,3-c][2,7]naphthyridine-2-carboxylate
N-[2-(1H-indol-3-yl)ethyl]-2-oxochromene-3-carboxamide
6-chloro-7-hydroxy-3,4-dimethyl-8-(piperidin-1-ylmethyl)chromen-2-one
4-chloro-N-[[1-(dimethylamino)cyclohexyl]methyl]-3-(furan-2-ylmethylsulfamoyl)benzamide
1-[[4-(2-oxopyrrolidin-1-yl)phenyl]methyl]-3-propylurea


In [7]:
from string import digits

# Remove elements from UPAC formulas
dataset = []
for i in UPAC_list:
    # Replace simbols with a coma
    new_list = i.translate(str.maketrans({'[': ' , ', ']': ' , ', 
                                         '(': ' , ', ')' : ' , ',
                                         '-': ' , ', ';' : ' , '}))
    
    new_str = new_list.translate(str.maketrans('', '', digits))
    dataset.append(new_str)
dataset

for item in dataset[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

ethyl  , amino , ,, , trimethyl ,  , morpholin ,  , yl , , , dihydrothieno , , , c ,  , , , naphthyridine ,  , carboxylate
N ,  ,  ,  , H , indol ,  , yl , ethyl ,  ,  , oxochromene ,  , carboxamide
 , chloro ,  , hydroxy , , , dimethyl ,  ,  , piperidin ,  , ylmethyl , chromen ,  , one
 , chloro , N ,  ,  ,  ,  , dimethylamino , cyclohexyl , methyl ,  ,  ,  , furan ,  , ylmethylsulfamoyl , benzamide
 ,  ,  ,  ,  ,  , oxopyrrolidin ,  , yl , phenyl , methyl ,  ,  , propylurea


In [8]:
# Convert the strings into list of strings
new_strings = []
for i in dataset:
    parsed_string = i.split(",")
    new_strings.append(parsed_string)
new_strings

for item in new_strings[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

['ethyl  ', ' amino ', ' ', '', ' ', ' trimethyl ', '  ', ' morpholin ', '  ', ' yl ', ' ', ' ', ' dihydrothieno ', ' ', ' ', ' c ', '  ', ' ', ' ', ' naphthyridine ', '  ', ' carboxylate']
['N ', '  ', '  ', '  ', ' H ', ' indol ', '  ', ' yl ', ' ethyl ', '  ', '  ', ' oxochromene ', '  ', ' carboxamide']
[' ', ' chloro ', '  ', ' hydroxy ', ' ', ' ', ' dimethyl ', '  ', '  ', ' piperidin ', '  ', ' ylmethyl ', ' chromen ', '  ', ' one']
[' ', ' chloro ', ' N ', '  ', '  ', '  ', '  ', ' dimethylamino ', ' cyclohexyl ', ' methyl ', '  ', '  ', '  ', ' furan ', '  ', ' ylmethylsulfamoyl ', ' benzamide']
[' ', '  ', '  ', '  ', '  ', '  ', ' oxopyrrolidin ', '  ', ' yl ', ' phenyl ', ' methyl ', '  ', '  ', ' propylurea']


In [9]:
from functools import reduce
# Convert list of lists in one list 
new_list = reduce(lambda a, b: a + b, new_strings)

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

ethyl  
 amino 
 

 


In [10]:
new_list = [s.replace(' ', '') for s in new_list]
for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

ethyl
amino





In [11]:
# Print the muber of left strings after reduction
print (len (new_list))

881223


In [12]:
# remove duplicates
from collections import OrderedDict

new_list = list(OrderedDict.fromkeys(new_list)) 

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

ethyl
amino

trimethyl
morpholin


In [13]:
# Remove one letter strings
new_list_columns = [x for x in new_list if len(x) >= 4]

for item in new_list_columns[:5]:   # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

ethyl
amino
trimethyl
morpholin
dihydrothieno


In [14]:
print (len (new_list_columns))

5039


In [15]:
new_list_columns.sort()
new_list_columns

['.....',
 'acenaphthyleno',
 'acetaldehyde',
 'acetamide',
 'acetamido',
 'acetamidoacetate',
 'acetamidoacetyl',
 'acetamidoacridin',
 'acetamidoanilino',
 'acetamidobenzenesulfonate',
 'acetamidobenzoate',
 'acetamidobenzoyl',
 'acetamidodecanedioate',
 'acetamidoethoxy',
 'acetamidoethyl',
 'acetamidomethyl',
 'acetamidophenoxy',
 'acetamidophenyl',
 'acetamidopropanoate',
 'acetamidopropanoylamino',
 'acetamidopyridin',
 'acetamidothiophen',
 'acetamidothiophene',
 'acetate',
 'aceticacid',
 'acetohydrazide',
 'acetonitrile',
 'acetyl',
 'acetylanilino',
 'acetylcarbamimidothioate',
 'acetylcarbamothioylamino',
 'acetylhydrazinyl',
 'acetylhydrazinylidene',
 'acetylimino',
 'acetylindol',
 'acetylindolizine',
 'acetyloxy',
 'acetyloxybenzoicacid',
 'acetyloxybenzoyl',
 'acetyloxyethylamino',
 'acetyloxymethyl',
 'acetyloxyphenyl',
 'acetyloxypropyl',
 'acetylphenoxy',
 'acetylphenyl',
 'acetylpiperazin',
 'acetylpiperazine',
 'acetylpiperidin',
 'acetylpyridin',
 'acetylsulfamoyl'

In [16]:
import numpy as np

dict_func_groups = dict.fromkeys(new_list_columns, 0)
dict_func_groups

{'.....': 0,
 'acenaphthyleno': 0,
 'acetaldehyde': 0,
 'acetamide': 0,
 'acetamido': 0,
 'acetamidoacetate': 0,
 'acetamidoacetyl': 0,
 'acetamidoacridin': 0,
 'acetamidoanilino': 0,
 'acetamidobenzenesulfonate': 0,
 'acetamidobenzoate': 0,
 'acetamidobenzoyl': 0,
 'acetamidodecanedioate': 0,
 'acetamidoethoxy': 0,
 'acetamidoethyl': 0,
 'acetamidomethyl': 0,
 'acetamidophenoxy': 0,
 'acetamidophenyl': 0,
 'acetamidopropanoate': 0,
 'acetamidopropanoylamino': 0,
 'acetamidopyridin': 0,
 'acetamidothiophen': 0,
 'acetamidothiophene': 0,
 'acetate': 0,
 'aceticacid': 0,
 'acetohydrazide': 0,
 'acetonitrile': 0,
 'acetyl': 0,
 'acetylanilino': 0,
 'acetylcarbamimidothioate': 0,
 'acetylcarbamothioylamino': 0,
 'acetylhydrazinyl': 0,
 'acetylhydrazinylidene': 0,
 'acetylimino': 0,
 'acetylindol': 0,
 'acetylindolizine': 0,
 'acetyloxy': 0,
 'acetyloxybenzoicacid': 0,
 'acetyloxybenzoyl': 0,
 'acetyloxyethylamino': 0,
 'acetyloxymethyl': 0,
 'acetyloxyphenyl': 0,
 'acetyloxypropyl': 0,
 'a

In [17]:
# https://stackoverflow.com/questions/28056171/how-to-build-and-fill-pandas-dataframe-from-for-loop
import copy
import re
dataset = []
data = []
# new_strings = []

list_formulas = df_cids['UPAC'].to_list()
for formula in list_formulas:
    new_list = re.findall(r'\b\w{4,}\b', formula)
    for group in new_list:
        # working
        new_dict = copy.deepcopy(dict_func_groups)
        for ii in new_list:
            if ii in new_dict.keys():
                new_dict[ii] +=1
                    
    id = formula
    # Combine all new features in an array
    # arr =[id, new_dict.values()]
    dataset.append(new_dict.values())

In [18]:
# Create an "index" column with the corresponding index values
df_iupac_target['index'] = df_iupac_target.index

# Display df_similarity
print('Shape of df_iupac_target ', df_iupac_target.shape)
df_iupac_target.head() 

Shape of df_iupac_target  (53536, 3)


UPAC  target  index
0  ethyl 1-amino-7,8,8-trimethyl-5-morpholin-4-yl...       0      0
1  N-[2-(1H-indol-3-yl)ethyl]-2-oxochromene-3-car...       0      1
2  6-chloro-7-hydroxy-3,4-dimethyl-8-(piperidin-1...       0      2
3  4-chloro-N-[[1-(dimethylamino)cyclohexyl]methy...       0      3
4  1-[[4-(2-oxopyrrolidin-1-yl)phenyl]methyl]-3-p...       0      4

In [19]:
df_func_groups = pd.DataFrame.from_dict(dataset,
                                        orient='columns',
                                        dtype=None, columns=None) 


df_func_groups.columns = new_list_columns
df_func_groups.head()

.....  acenaphthyleno  acetaldehyde  acetamide  acetamido  \
0      0               0             0          0          0   
1      0               0             0          0          0   
2      0               0             0          0          0   
3      0               0             0          0          0   
4      0               0             0          0          0   

   acetamidoacetate  acetamidoacetyl  acetamidoacridin  acetamidoanilino  \
0                 0                0                 0                 0   
1                 0                0                 0                 0   
2                 0                0                 0                 0   
3                 0                0                 0                 0   
4                 0                0                 0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidodecanedioate  acetamidoethoxy  acetamidoethyl  acetamidomethyl  \
0                      0                0               0                0   
1                      0                0               0                0   
2                      0                0               0                0   
3                      0                0               0                0   
4                      0                0               0                0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  \
0                 0                0                    0   
1                 0                0                    0   
2                 0                0                    0   
3                 0                0                    0   
4                 0                0                    0   

   acetamidopropanoylamino  acetamidopyridin  acetamidothiophen  \
0                        0                 0                  0   
1                        0                 0                  0   
2                        0                 0                  0   
3                        0                 0                  0   
4                        0                 0                  0   

   acetamidothiophene  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                   0        0           0               0             0   
1                   0        0           0               0             0   
2                   0        0           0               0             0   
3                   0        0           0               0             0   
4                   0        0           0               0             0   

   acetyl  acetylanilino  acetylcarbamimidothioate  acetylcarbamothioylamino  \
0       0              0                         0                         0   
1       0              0                         0                         0   
2       0              0                         0                         0   
3       0              0                         0                         0   
4       0              0                         0                         0   

   acetylhydrazinyl  acetylhydrazinylidene  acetylimino  acetylindol  \
0                 0                      0            0            0   
1                 0                      0            0            0   
2                 0                      0            0            0   
3                 0                      0            0            0   
4                 0                      0            0            0   

   acetylindolizine  acetyloxy  acetyloxybenzoicacid  acetyloxybenzoyl  \
0                 0          0                     0          

In [20]:
# Create an "index" column with the corresponding index values
df_func_groups['index'] = df_func_groups.index

# Convert the index values into strings
# df_func_groups['index'] = df_func_groups['index'].astype(str)

# Display df_similarity
print('Shape of df_func_groups: ', df_func_groups.shape)
df_func_groups.head() 

Shape of df_func_groups:  (53536, 5040)


.....  acenaphthyleno  acetaldehyde  acetamide  acetamido  \
0      0               0             0          0          0   
1      0               0             0          0          0   
2      0               0             0          0          0   
3      0               0             0          0          0   
4      0               0             0          0          0   

   acetamidoacetate  acetamidoacetyl  acetamidoacridin  acetamidoanilino  \
0                 0                0                 0                 0   
1                 0                0                 0                 0   
2                 0                0                 0                 0   
3                 0                0                 0                 0   
4                 0                0                 0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidodecanedioate  acetamidoethoxy  acetamidoethyl  acetamidomethyl  \
0                      0                0               0                0   
1                      0                0               0                0   
2                      0                0               0                0   
3                      0                0               0                0   
4                      0                0               0                0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  \
0                 0                0                    0   
1                 0                0                    0   
2                 0                0                    0   
3                 0                0                    0   
4                 0                0                    0   

   acetamidopropanoylamino  acetamidopyridin  acetamidothiophen  \
0                        0                 0                  0   
1                        0                 0                  0   
2                        0                 0                  0   
3                        0                 0                  0   
4                        0                 0                  0   

   acetamidothiophene  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                   0        0           0               0             0   
1                   0        0           0               0             0   
2                   0        0           0               0             0   
3                   0        0           0               0             0   
4                   0        0           0               0             0   

   acetyl  acetylanilino  acetylcarbamimidothioate  acetylcarbamothioylamino  \
0       0              0                         0                         0   
1       0              0                         0                         0   
2       0              0                         0                         0   
3       0              0                         0                         0   
4       0              0                         0                         0   

   acetylhydrazinyl  acetylhydrazinylidene  acetylimino  acetylindol  \
0                 0                      0            0            0   
1                 0                      0            0            0   
2                 0                      0            0            0   
3                 0                      0            0            0   
4                 0                      0            0            0   

   acetylindolizine  acetyloxy  acetyloxybenzoicacid  acetyloxybenzoyl  \
0                 0          0                     0          

In [21]:
# Add the new data frame df_similarity to the already existing df based on "index"
df = pd.merge(df_iupac_target,df_func_groups, on=['index'])

# Display df_similarity
print('Shape of df: ', df.shape)
df.head()

Shape of df:  (53534, 5042)


UPAC  target  index  .....  \
0  ethyl 1-amino-7,8,8-trimethyl-5-morpholin-4-yl...       0      0      0   
1  N-[2-(1H-indol-3-yl)ethyl]-2-oxochromene-3-car...       0      1      0   
2  6-chloro-7-hydroxy-3,4-dimethyl-8-(piperidin-1...       0      2      0   
3  4-chloro-N-[[1-(dimethylamino)cyclohexyl]methy...       0      3      0   
4  1-[[4-(2-oxopyrrolidin-1-yl)phenyl]methyl]-3-p...       0      4      0   

   acenaphthyleno  acetaldehyde  acetamide  acetamido  acetamidoacetate  \
0               0             0          0          0                 0   
1               0             0          0          0                 0   
2               0             0          0          0                 0   
3               0             0          0          0                 0   
4               0             0          0          0                 0   

   acetamidoacetyl  acetamidoacridin  acetamidoanilino  \
0                0                 0                 0   
1                0                 0                 0   
2                0                 0                 0   
3                0                 0                 0   
4                0                 0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidodecanedioate  acetamidoethoxy  acetamidoethyl  acetamidomethyl  \
0                      0                0               0                0   
1                      0                0               0                0   
2                      0                0               0                0   
3                      0                0               0                0   
4                      0                0               0                0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  \
0                 0                0                    0   
1                 0                0                    0   
2                 0                0                    0   
3                 0                0                    0   
4                 0                0                    0   

   acetamidopropanoylamino  acetamidopyridin  acetamidothiophen  \
0                        0                 0                  0   
1                        0                 0                  0   
2                        0                 0                  0   
3                        0                 0                  0   
4                        0                 0                  0   

   acetamidothiophene  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                   0        0           0               0             0   
1                   0        0           0               0             0   
2                   0        0           0               0             0   
3                   0        0           0               0             0   
4                   0        0           0               0             0   

   acetyl  acetylanilino  acetylcarbamimidothioate  acetylcarbamothioylamino  \
0       0              0                         0                         0   
1       0              0                         0                         0   
2       0              0                         0                         0   
3       0              0                         0                         0   
4       0              0                         0                         0   

   acetylhydrazinyl  acetylhydrazinylidene  acetylimino  acetylindol  \
0                 0                      0            0            0   
1                 0                      0 

In [22]:
df.to_csv('df4_for_final.csv')

In [23]:
# Drop the CID and UPAC columns by name
df = df.drop(columns=['UPAC', 'index'],axis=1) 

In [24]:
# Display the data frame
print('Shape of the data frame: ', df.shape)
df.head()

Shape of the data frame:  (53534, 5040)


target  .....  acenaphthyleno  acetaldehyde  acetamide  acetamido  \
0       0      0               0             0          0          0   
1       0      0               0             0          0          0   
2       0      0               0             0          0          0   
3       0      0               0             0          0          0   
4       0      0               0             0          0          0   

   acetamidoacetate  acetamidoacetyl  acetamidoacridin  acetamidoanilino  \
0                 0                0                 0                 0   
1                 0                0                 0                 0   
2                 0                0                 0                 0   
3                 0                0                 0                 0   
4                 0                0                 0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidodecanedioate  acetamidoethoxy  acetamidoethyl  acetamidomethyl  \
0                      0                0               0                0   
1                      0                0               0                0   
2                      0                0               0                0   
3                      0                0               0                0   
4                      0                0               0                0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  \
0                 0                0                    0   
1                 0                0                    0   
2                 0                0                    0   
3                 0                0                    0   
4                 0                0                    0   

   acetamidopropanoylamino  acetamidopyridin  acetamidothiophen  \
0                        0                 0                  0   
1                        0                 0                  0   
2                        0                 0                  0   
3                        0                 0                  0   
4                        0                 0                  0   

   acetamidothiophene  acetate  aceticacid  acetohydrazide  acetonitrile  \
0                   0        0           0               0             0   
1                   0        0           0               0             0   
2                   0        0           0               0             0   
3                   0        0           0               0             0   
4                   0        0           0               0             0   

   acetyl  acetylanilino  acetylcarbamimidothioate  acetylcarbamothioylamino  \
0       0              0                         0                         0   
1       0              0                         0                         0   
2       0              0                         0                         0   
3       0              0                         0                         0   
4       0              0                         0                         0   

   acetylhydrazinyl  acetylhydrazinylidene  acetylimino  acetylindol  \
0                 0                      0            0            0   
1                 0                      0            0            0   
2                 0                      0            0            0   
3                 0                      0            0            0   
4                 0                      0            0            0   

   acetylindolizine  acetyloxy  acetyloxybenzoicacid  acetyloxybenzoyl  \
0             

In [25]:
df.to_csv('df4_targets_IUPACs.csv')